## Import Libraries

In [6]:
from genericpath import exists
import pdb
from pickletools import uint8
from turtle import pd
import torchvision
import torch
import os
import sys
sys.path.insert(0, '../')
#from models.model_mrcnn import _default_mrcnn_config, build_default
import torchvision
import torch
from models_pytorch_lightning.generalized_mask_rcnn_pl import LitMaskRCNN

# from torchknickknacks import modelutils
from PIL import Image
import matplotlib.pyplot as plt
from torchvision import transforms
from pytorch_grad_cam.utils.image import show_cam_on_image

import numpy as np
import cv2
import requests
import random
import glob
from skimage.measure import label, regionprops, regionprops_table
from skimage import data, filters, measure, morphology
import pandas as pd
import wandb
from tqdm import tqdm
from skimage import data
from skimage.color import rgb2hed, hed2rgb

In [7]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
import plotly.graph_objects as go
from sklearn.metrics import roc_curve, auc
from sklearn.metrics import precision_recall_curve

## Utility Functions

In [8]:
class GetExternalDataOutput():
    
    # TODO fix the visualization flags
    def __init__(self, model, test_input_path, detection_threshold):
        self.model = model
        self.test_input_path = test_input_path
        self.detection_threshold = detection_threshold
        self.class_names = ['Cored', 'Diffuse', 'Coarse-Grained', 'CAA']
        self.class_to_colors = {'Cored': (255, 0, 0), 'Diffuse' : (0, 0, 255), 'Coarse-Grained': (0,255,0), 'CAA':(225, 255, 0)}
        #TODO change this to nas location later
        self.result_save_dir= "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/Results-Nature/"
        self.colors = np.random.uniform(0, 255, size=(len(self.class_names), 3))
    

    def get_outputs_nms(self, input_tensor, model, score_threshold = 0.5, iou_threshold = 0.5):
        #mask_list = []
        #label_list = []
        #score_list =[]
        #box_list = []
        with torch.no_grad():
            # forward pass of the image through the modle
            outputs = model(input_tensor)
        boxes = outputs[0]['boxes']
        labels = outputs[0]['labels']
        scores = outputs[0]['scores']
        masks = outputs[0]['masks']
        #print(boxes.shape,labels.shape, masks.shape)
        # Apply score threshold
        keep = scores > score_threshold
        boxes, labels, scores, masks = boxes[keep], labels[keep], scores[keep], masks[keep]
        #print(boxes.shape,labels.shape, masks.shape)
        #print(keep)
        keep = torchvision.ops.nms(boxes, scores, iou_threshold)
        boxes, labels, scores, masks = boxes[keep], labels[keep], scores[keep], masks[keep]
        #print(keep)
        #print(boxes.shape,labels.shape, masks.shape)
        scores = list(scores.detach().cpu().numpy())
        #print(scores)
        masks = list((masks>0.5).detach().cpu().numpy())
        #masks = list((masks>0.5).squeeze().detach().cpu().numpy())
        #print(masks.shape)
        boxes = [[(int(i[0]), int(i[1])), (int(i[2]), int(i[3]))]  for i in boxes.detach().cpu()]
        labels = list(labels.detach().cpu().numpy())
        labels = [self.class_names[i-1] for i in labels]
        return masks, boxes, labels, scores



    def prepare_input(self, image):
        image_float_np = np.float32(image) / 255
        # define the torchvision image transforms
        transform = torchvision.transforms.Compose([
            torchvision.transforms.Resize(1024),
            torchvision.transforms.ToTensor(),
        ])
        input_tensor = transform(transforms.ToPILImage()(image))
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        input_tensor = input_tensor.to(device)
        # Add a batch dimension:
        input_tensor = input_tensor.unsqueeze(0)
        return input_tensor, image_float_np


    def generate_results(self):
        # This will help us create a different color for each class
        # Load Trained 
        
        #self.model.load_state_dict(torch.load(self.model_input_path))
    
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        
        self.model.eval().to(device)
        output_dict=dict()
        output_score=dict()
        

        test_folders = glob.glob(os.path.join(self.test_input_path, "*"))
        
        # Test images from each WSI folder
        test_folders = sorted(test_folders)
        
        print("length of test folders", len(test_folders))
        
        output_dict = dict()
      
        for test_folder in tqdm(test_folders):

            print("\n", test_folder)
            
            folder_name = os.path.basename(test_folder)

            if folder_name == "labels":
                continue

            # make all necessary folders
            #self.make_result_dirs(folder_name)
            images = glob.glob(os.path.join(test_folder, '*.jpg'))
            
            print("Images in Test Folder", len(images))
            i = 0

            for img in tqdm(images):
                result_img = 0
                img_name = os.path.basename(img).split('.')[0]
                
                image = np.array(Image.open(img))

                #total_image_pixels+= image.shape[0] * image.shape[1]
                # Check if image has alpha channel
                if image.shape[2] == 4:
                    image = image[:,:, :3]
                input_tensor, image_float_np = self.prepare_input(image)

                masks, boxes, labels, scores = self.get_outputs_nms(input_tensor, self.model, 0.1, 0.25)
                #print(labels, scores)
                #print(labels)
                output_dict[img_name] = labels
                output_score[img_name]=scores
        return output_dict, output_score
    
    def generate_results_per_image(self):
        # This will help us create a different color for each class
        # Load Trained 
        output_dict=dict()
        output_score=dict()
        
        self.model.load_state_dict(torch.load(self.model_input_path))
    
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.model.eval().to(device)
        output_dict=dict()
        output_score=dict()
        test_folders = glob.glob(os.path.join("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB", "*.jpg"))
        print(len(test_folders))
        #for Finkbeiner-Steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB 
        for img in  test_folders:
            #img = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB/NA4751-02_AB_19_6_34.jpg"
            #img = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/amyb_wsi/train/images/A_0_0_XE10-045_1_AmyB_1_49175x_54069y_image.png"
            img_name = os.path.basename(img).split('.')[0]
            image = np.array(Image.open(img))

            #total_image_pixels+= image.shape[0] * image.shape[1]
            # Check if image has alpha channel
            if image.shape[2] == 4:
                image = image[:,:, :3]
            input_tensor, image_float_np = self.prepare_input(image)

            masks, boxes, labels, scores = self.get_outputs_nms(input_tensor, self.model, 0.25, 0.25)
            #print(labels, scores)
            #print(labels)
            output_dict[img_name] = labels
            output_score[img_name]=scores
        return output_dict, output_score


## Evaluate External Dataset

In [9]:
image_dataset =  "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train"

gt_train = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train.csv"

#gt_val = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/validation.csv"

#gt_hold_out =  "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/hold-out.csv"

model_name = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/runpod_mrcnn_models/yp2mf3i8_epoch=108-step=872.ckpt"
model = LitMaskRCNN.load_from_checkpoint(model_name)

In [11]:
def evaluate_output(gt_train, output_df, output_score, train_flag):
    gt_train_df = pd.read_csv(gt_train)
    gt_train_df["imagename2"]= gt_train_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))
    if train_flag:
        gt_train_df["cored_gt"] = gt_train_df["cored_bool"].apply(lambda l: 1 if l==True else 0)
        gt_train_df["diffuse_gt"] = gt_train_df["diffuse_bool"].apply(lambda l: 1 if l==True else 0)
        gt_train_df["CAA_gt"] = gt_train_df["CAA_bool"].apply(lambda l: 1 if l==True else 0)
    else:
        gt_train_df["cored_gt"] = gt_train_df["cored"].apply(lambda l: 1 if l>=1 else 0)
        gt_train_df["diffuse_gt"] = gt_train_df["diffuse"].apply(lambda l: 1 if l>=1 else 0)
        gt_train_df["CAA_gt"] = gt_train_df["CAA"].apply(lambda l: 1 if l>=1 else 0)
        
    gt_train_df["cored_pred"] = 0
    gt_train_df["diffuse_pred"] = 0
    gt_train_df["CAA_pred"] = 0
    
    def assign_pred_scores(row, val):
        if row["imagename2"] in output_df.keys():
            l = output_df[row["imagename2"]]
            s = output_score[row["imagename2"]]
            indices = [i for i in range(len(l)) if l[i] == val]
            s_selected = [ s[i] for i in indices]
            if len(s_selected)!=0:
                return max(s_selected)
            else:
                return 0
        else:
            return None
    
    gt_train_df["cored_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Cored"), axis=1)
    gt_train_df["diffuse_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Diffuse"),axis=1)
    gt_train_df["cg_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Coarse-Grained"),axis=1)
    gt_train_df["CAA_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "CAA"),axis=1)
    
    def assign_pred_labels(row, val):
        if row["imagename2"] in output_df.keys():
            l = output_df[row["imagename2"]]
            if val in l:
                return 1
            else:
                return 0
        else:
            return None
    
    gt_train_df["cored_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Cored"), axis=1)
    gt_train_df["diffuse_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Diffuse"),axis=1)
    gt_train_df["cg_score"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Coarse-Grained"),axis=1)
    gt_train_df["CAA_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "CAA"),axis=1)
    return gt_train_df
    

In [12]:

explain = GetExternalDataOutput(model, test_input_path=image_dataset, detection_threshold=0.6)
output_df, output_scores = explain.generate_results()


length of test folders 29


  0%|          | 0/29 [00:00<?, ?it/s]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4009-02_AB
Images in Test Folder 3897


  3%|▎         | 1/29 [08:12<3:50:00, 492.89s/it]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4072-02_AB
Images in Test Folder 344


...

 93%|█████████▎| 27/29 [2:00:30<04:06, 123.25s/it]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA_4883_02_AB
Images in Test Folder 253


 97%|█████████▋| 28/29 [2:01:02<01:35, 95.79s/it] 


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA_4888_02_AB17-24
Images in Test Folder 3675


100%|██████████| 29/29 [2:08:47<00:00, 266.45s/it]


In [8]:
output_df


{'NA4009-02_AB_22_21_50': ['Coarse-Grained'],
 'NA4009-02_AB_10_27_31': ['Diffuse', 'CAA', 'CAA', 'Diffuse', 'Diffuse'],
 'NA4009-02_AB_10_21_74': ['Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse'],
 'NA4009-02_AB_7_16_12': ['Diffuse'],
 'NA4009-02_AB_8_4_2': ['Diffuse'],
 'NA4009-02_AB_20_11_25': ['Diffuse', 'Diffuse', 'Diffuse', 'Diffuse'],
 'NA4009-02_AB_26_16_34': ['Diffuse'],
 'neg_NA4009-02_AB_5_21_2': [],
 'NA4009-02_AB_23_16_4': ['Diffuse'],
 'NA4009-02_AB_15_20_10': [],
 'NA4009-02_AB_5_29_26': [],
 'NA4009-02_AB_6_26_62': ['Coarse-Grained', 'Coarse-Grained'],
 'NA4009-02_AB_6_28_54': ['Diffuse'],
 'NA4009-02_AB_17_6_71': ['Diffuse'],
 'NA4009-02_AB_6_21_22': ['Diffuse', 'Diffuse', 'Diffuse', 'CAA'],
 'NA4009-02_AB_15_35_15': ['Diffuse', 'Diffuse'],
 'NA4009-02_AB_24_22_27': ['Diffuse'],
 'neg_NA4009-02_AB_13_19_3': ['Diffuse', 'Diffuse', 'Diffuse'],
 'NA4009-02_AB_6_28_10': ['CAA', 'Diffuse', 'Diffuse'],
 'NA4009-02_AB_7_10_65': ['CAA', 

In [8]:
output_scores

{'NA4009-02_AB_22_21_50': [0.77416444],
 'NA4009-02_AB_10_27_31': [0.86789554, 0.8321429, 0.8238295],
 'NA4009-02_AB_10_21_74': [0.9111257,
  0.7572885,
  0.72732615,
  0.6137131,
  0.5296569,
  0.32546493],
 'NA4009-02_AB_7_16_12': [],
 'NA4009-02_AB_8_4_2': [0.9025852],
 'NA4009-02_AB_20_11_25': [0.7187162],
 'NA4009-02_AB_26_16_34': [0.96922016],
 'neg_NA4009-02_AB_5_21_2': [],
 'NA4009-02_AB_23_16_4': [0.77968335],
 'NA4009-02_AB_15_20_10': [],
 'NA4009-02_AB_5_29_26': [],
 'NA4009-02_AB_6_26_62': [0.8132504, 0.65848386],
 'NA4009-02_AB_6_28_54': [0.6911069],
 'NA4009-02_AB_17_6_71': [0.40255526],
 'NA4009-02_AB_6_21_22': [0.8727435, 0.85925335, 0.81067234, 0.72591937],
 'NA4009-02_AB_15_35_15': [0.65485454],
 'NA4009-02_AB_24_22_27': [],
 'neg_NA4009-02_AB_13_19_3': [],
 'NA4009-02_AB_6_28_10': [0.9072429, 0.8151504],
 'NA4009-02_AB_7_10_65': [0.98147935, 0.32454327],
 'neg_NA4009-02_AB_6_35_4': [],
 'NA4009-02_AB_28_33_16': [0.9028534],
 'NA4009-02_AB_9_19_6': [0.95370555],
 'NA4

In [9]:
model_output_df = pd.DataFrame(columns=["imagename2","label_pred","score_pred"])
for k,v in output_df.items():
    for j in range(len(v)):
        model_output_df.loc[len(model_output_df)] = [k, v[j], output_scores[k][j]]

In [ ]:
model_output_df

imagename2      label_pred  score_pred
0           NA4009-02_AB_22_21_50  Coarse-Grained    0.756591
1           NA4009-02_AB_10_27_31         Diffuse    0.872735
2           NA4009-02_AB_10_27_31             CAA    0.842058
3           NA4009-02_AB_10_27_31             CAA    0.806063
4           NA4009-02_AB_10_27_31         Diffuse    0.201708
...                           ...             ...         ...
124271  NA_4888_02_AB17-24_8_15_4         Diffuse    0.922207
124272  NA_4888_02_AB17-24_8_15_4         Diffuse    0.905630
124273  NA_4888_02_AB17-24_8_15_4         Diffuse    0.895952
124274  NA_4888_02_AB17-24_8_15_4         Diffuse    0.517312
124275  NA_4888_02_AB17-24_7_14_1         Diffuse    0.553253

[124276 rows x 3 columns]

In [11]:
model_output_agg = model_output_df.groupby(["imagename2","label_pred"]).count().reset_index()

In [12]:
model_output_agg.head(2)

imagename2 label_pred  score_pred
0  NA4009-02_AB_10_10_14    Diffuse           2
1  NA4009-02_AB_10_10_15        CAA           1

In [13]:
model_output_agg1  = model_output_agg.pivot(index='imagename2', columns='label_pred')['score_pred'].reset_index()

In [14]:
model_output_agg1.columns = ['imagename2', 'CAA_pred', 'Coarse-Grained_pred', 'Cored_pred', 'Diffuse_pred']

In [15]:
model_output_agg1 = model_output_agg1.fillna(0)

In [16]:
gt_train_df = pd.read_csv(gt_train)
gt_train_df["imagename2"]= gt_train_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))

In [17]:
gt_train_df1 = gt_train_df[gt_train_df["negative"]!=1]

In [18]:
model_output_agg2 = pd.merge(model_output_agg1, gt_train_df1, how="left", on="imagename2")

In [19]:
model_output_agg = pd.merge(model_output_agg, gt_train_df1, how="left", on="imagename2")

In [20]:
model_output_agg2 = model_output_agg2[~model_output_agg2["imagename"].isna()]

In [20]:
model_output_agg2["CAA_pred"].sum()

15992.0

In [21]:
model_output_agg2["CAA"].sum()/model_output_agg2["CAA_pred"].sum()

0.1641655647071954

In [22]:
model_output_agg2["Diffuse_pred"].sum()/model_output_agg2["diffuse"].sum()

1.1559567669047746

In [23]:
model_output_agg2["Cored_pred"].sum()/model_output_agg2["cored"].sum()

1.298166968926798

In [24]:
model_output_agg2["Cored_pred"].sum()

3316.0

In [25]:
model_output_agg2["cored"].sum()

2554.370954871357

In [26]:
model_output_agg2["cored1"] = model_output_agg2["cored"].astype(int)

In [27]:
model_output_agg2.head(2)

imagename2  CAA_pred  Coarse-Grained_pred  Cored_pred  \
0  NA4009-02_AB_10_10_14       0.0                  0.0         0.0   
1  NA4009-02_AB_10_10_15       1.0                  0.0         0.0   

   Diffuse_pred       id                               imagename  cored  \
0           2.0  19548.0  NA4009-02_AB/NA4009-02_AB_10_10_14.jpg    0.0   
1           0.0  19549.0  NA4009-02_AB/NA4009-02_AB_10_10_15.jpg    0.0   

    diffuse  CAA  negative      flag  notsure  cored1  
0  2.653226  0.0       0.0  1.000000      0.0       0  
1  3.033079  0.0       0.0  0.426829      0.0       0

In [28]:
model_output_agg2["Coarse-Grained_pred"] = model_output_agg2["Coarse-Grained_pred"].astype(float)

In [29]:
model_output_agg2["cored_match"] = model_output_agg2.apply(lambda l: min(l["Cored_pred"],l["cored"]), axis=1)

In [35]:
model_output_agg2["cored_match"].sum()/model_output_agg2["Cored_pred"].sum()

0.1893518525696403

In [36]:
model_output_agg2["cored_match"].sum()/model_output_agg2["Cored_pred"].sum()

0.1893518525696403

In [37]:
model_output_agg2["cored_match"].sum()/model_output_agg2["Coarse-Grained_pred"].sum()

0.10545696055104589

In [38]:
model_output_agg2["cored_match"].sum()/model_output_agg2["cored"].sum()

0.24581032051100388

In [39]:
model_output_agg2["cored_match"].sum()/model_output_agg2["cored"].sum()

0.24581032051100388

In [40]:
model_output_agg2["diffuse_match"] = model_output_agg2.apply(lambda l: min(l["Diffuse_pred"],l["diffuse"]), axis=1)

In [41]:
model_output_agg2["diffuse_match"].sum()/model_output_agg2["diffuse"].sum()

0.7264142389859793

In [42]:
model_output_agg2["diffuse_match"].sum()/model_output_agg2["diffuse"].sum()

0.7264142389859793

In [43]:
model_output_agg2["diffuse_match"].sum()/model_output_agg2["Diffuse_pred"].sum()

0.628409521690892

In [44]:
model_output_agg2["caa_match"] = model_output_agg2.apply(lambda l: min(l["CAA_pred"],l["CAA"]), axis=1)

In [45]:
model_output_agg2["caa_match"].sum()/model_output_agg2["CAA_pred"].sum()

0.07025870373748977

In [46]:
model_output_agg2["caa_match"].sum()/model_output_agg2["CAA_pred"].sum()

0.07025870373748977

In [47]:
model_output_agg2["caa_match"].sum()/model_output_agg2["CAA"].sum()

0.4279746721719791

In [42]:
gt_val_df = pd.read_csv(gt_val)
gt_val_df["imagename2"]= gt_val_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))

In [43]:
gt_hold_out_df = pd.read_csv(gt_hold_out)
gt_hold_out_df["imagename2"]= gt_hold_out_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))

In [44]:
gt_train_df = pd.concat([gt_train_df,gt_val_df,gt_hold_out_df],axis=0)

In [12]:
model_output_df1 = pd.merge(model_output_df, gt_train_df[["imagename","imagename2"]], how="left", on="imagename2")

In [13]:
model_output_df1["folder_name"] = model_output_df1["imagename"].apply(lambda l: str(l).split("/")[0])

In [47]:
model_output_df1[model_output_df1["folder_name"]=="NA4009-02_AB"]

imagename2      label_pred  score_pred  \
385   NA4009-02_AB_22_21_50  Coarse-Grained    0.774164   
386   NA4009-02_AB_10_27_31         Diffuse    0.867896   
387   NA4009-02_AB_10_27_31             CAA    0.832143   
388   NA4009-02_AB_10_27_31             CAA    0.823829   
389   NA4009-02_AB_10_21_74         Diffuse    0.911126   
...                     ...             ...         ...   
6274  NA4009-02_AB_21_35_42         Diffuse    0.805553   
6275  NA4009-02_AB_21_35_42         Diffuse    0.747272   
6276  NA4009-02_AB_21_35_42         Diffuse    0.566200   
6277  NA4009-02_AB_21_35_42         Diffuse    0.547035   
6278  NA4009-02_AB_23_34_15         Diffuse    0.979649   

                                   imagename   folder_name  
385   NA4009-02_AB/NA4009-02_AB_22_21_50.jpg  NA4009-02_AB  
386   NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
387   NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
388   NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
389   NA4009-02_AB/NA4009-02_AB_10_21_74.jpg  NA4009-02_AB  
...                                      ...           ...  
6274  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
6275  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
6276  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
6277  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
6278  NA4009-02_AB/NA4009-02_AB_23_34_15.jpg  NA4009-02_AB  

[5894 rows x 5 columns]

In [14]:
len(model_output_df1)

89632

In [15]:
# running train dataset
gt_train_df = evaluate_output(gt_train, output_df, output_scores, False)

In [53]:
# running train dataset
gt_train_df = evaluate_output(gt_train, output_df, output_scores, False)
gt_val_df = evaluate_output(gt_val, output_df, output_scores, False)
gt_hold_out_df = evaluate_output(gt_hold_out, output_df, output_scores, False)

In [54]:
gt_train_df = pd.concat([gt_train_df,gt_val_df,gt_hold_out_df],axis=0)

In [99]:
gt_train_df

id                                          imagename     cored  \
0          0           NA4009-02_AB/neg_NA4009-02_AB_0_10_4.jpg  0.000000   
1          0           NA4009-02_AB/neg_NA4009-02_AB_0_11_2.jpg  0.000000   
2          0           NA4009-02_AB/neg_NA4009-02_AB_0_16_2.jpg  0.000000   
3          0           NA4009-02_AB/neg_NA4009-02_AB_0_25_2.jpg  0.000000   
4      19548             NA4009-02_AB/NA4009-02_AB_10_10_14.jpg  0.000000   
...      ...                                                ...       ...   
10868  10935  NA4974-02_AB17-24/NA4974-02_AB17-24_8_29.jpg_5...  0.000000   
10869  10936  NA4974-02_AB17-24/NA4974-02_AB17-24_8_29.jpg_6...  0.000000   
10870  10937  NA4974-02_AB17-24/NA4974-02_AB17-24_8_29.jpg_7...  0.375235   
10871  10938  NA4974-02_AB17-24/NA4974-02_AB17-24_8_29.jpg_8...  0.000000   
10872  10939  NA4974-02_AB17-24/NA4974-02_AB17-24_8_29.jpg_9...  0.000000   

        diffuse  CAA  negative  flag  notsure                imagename2  \
0      0.000000  0.0       1.0   0.0      0.0   neg_NA4009-02_AB_0_10_4   
1      0.000000  0.0       1.0   0.0      0.0   neg_NA4009-02_AB_0_11_2   
2      0.000000  0.0       1.0   0.0      0.0   neg_NA4009-02_AB_0_16_2   
3      0.000000  0.0       1.0   0.0      0.0   neg_NA4009-02_AB_0_25_2   
4      2.653226  0.0       0.0   1.0      0.0     NA4009-02_AB_10_10_14   
...         ...  ...       ...   ...      ...                       ...   
10868  2.000000  0.0       0.0   2.0      0.0  NA4974-02_AB17-24_8_29_5   
10869  2.000000  0.0       0.0   0.0      0.0  NA4974-02_AB17-24_8_29_6   
10870  1.000000  0.0       0.0   1.0      0.0  NA4974-02_AB17-24_8_29_7   
10871  3.000000  0.0       0.0   2.0      0.0  NA4974-02_AB17-24_8_29_8   
10872  2.000000  0.0       0.0   1.0      0.0  NA4974-02_AB17-24_8_29_9   

       cored_gt  diffuse_gt  CAA_gt cored_pred diffuse_pred CAA_pred  \
0             0           0       0          0            0        0   
1             0           0       0          0            0        0   
2             0           0       0          0            0        0   
3             0           0       0          0            0        0   
4             0           1       0          0            1        0   
...         ...         ...     ...        ...          ...      ...   
10868         0           1       0       None         None     None   
10869         0           1       0       None         None     None   
10870         1           1       0       None         None     None   
10871         0           1       0       None         None     None   
10872         0           1       0       None         None     None   

      cored_score diffuse_score cg_score CAA_score  
0             0.0           0.0        0       0.0  
1             0.0           0.0        0       0.0  
2             0.0           0.0        0       0.0  
3             0.0           0.0        0       0.0  
4             0.0      0.843813        0       0.0  
...           ...           ...      ...       ...  
10868        None          None     None      None  
10869        None          None     None      None  
10870        None          None     None      None  
10871        None          None     None      None  
10872        None          None     None      None  

[80873 rows x 19 columns]

In [16]:
# excluding NA values from val
notna_gt_train_df = gt_train_df[~gt_train_df["cored_pred"].isna()]

In [17]:
notna_gt_train_df["cored_gt"] = notna_gt_train_df["cored"].apply(lambda l: 1 if l>=1 else 0)
notna_gt_train_df["diffuse_gt"] = notna_gt_train_df["diffuse"].apply(lambda l: 1 if l>=1 else 0)
notna_gt_train_df["CAA_gt"] = notna_gt_train_df["CAA"].apply(lambda l: 1 if l>=1 else 0)

In [18]:
notna_gt_train_df["imagename"].nunique()

61370

In [147]:
notna_gt_train_df["cored_pred2"] = np.where( (notna_gt_train_df["cored_pred"]>0) | (notna_gt_train_df["cg_score"]>=0.6), 1,0)

/tmp/ipykernel_14394/2041043708.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [148]:
cored1 = notna_gt_train_df[notna_gt_train_df["cored_gt"]>0]

In [149]:
cored1

id                                         imagename  cored  \
90    14215             NA4009-02_AB/NA4009-02_AB_10_24_0.jpg    1.0   
208    5770             NA4009-02_AB/NA4009-02_AB_10_7_65.jpg    1.0   
779    2832             NA4009-02_AB/NA4009-02_AB_13_9_59.jpg    1.0   
904    3245            NA4009-02_AB/NA4009-02_AB_14_8_106.jpg    1.0   
1049   2194              NA4009-02_AB/NA4009-02_AB_15_9_3.jpg    1.0   
...     ...                                               ...    ...   
8440   9905  NA_4930_02_AB14-24/NA_4930_02_AB14-24_9_3_27.jpg    1.0   
8479   4933  NA_4930_02_AB14-24/NA_4930_02_AB14-24_9_7_15.jpg    1.0   
8502  22879  NA_4933_02_AB17-24/NA_4933_02_AB17-24_11_6_2.jpg    1.0   
8505   5367  NA_4933_02_AB17-24/NA_4933_02_AB17-24_11_7_1.jpg    1.0   
8523   4785  NA_4933_02_AB17-24/NA_4933_02_AB17-24_14_5_1.jpg    1.0   

       diffuse  CAA  negative  flag  notsure                 imagename2  \
90    0.000000  0.0       0.0   0.0      0.0       NA4009-02_AB_10_24_0   
208   0.000000  0.0       0.0   0.0      0.0       NA4009-02_AB_10_7_65   
779   0.425000  0.0       0.0   0.0      0.0       NA4009-02_AB_13_9_59   
904   0.000000  0.0       0.0   0.0      0.0      NA4009-02_AB_14_8_106   
1049  0.110608  0.0       0.0   0.0      0.0        NA4009-02_AB_15_9_3   
...        ...  ...       ...   ...      ...                        ...   
8440  0.596367  0.0       0.0   0.0      0.0  NA_4930_02_AB14-24_9_3_27   
8479  0.066406  0.0       0.0   0.0      0.0  NA_4930_02_AB14-24_9_7_15   
8502  0.000000  0.0       0.0   0.0      0.0  NA_4933_02_AB17-24_11_6_2   
8505  0.000000  0.0       0.0   0.0      0.0  NA_4933_02_AB17-24_11_7_1   
8523  0.000000  0.0       0.0   0.0      0.0  NA_4933_02_AB17-24_14_5_1   

      cored_gt  diffuse_gt  CAA_gt  cored_pred diffuse_pred CAA_pred  \
90           1           0       0           0            1        0   
208          1           0       0           1            0        0   
779          1           0       0           1            0        1   
904          1           0       0           0            0        0   
1049         1           0       0           1            0        0   
...        ...         ...     ...         ...          ...      ...   
8440         1           0       0           0            0        1   
8479         1           0       0           0            1        1   
8502         1           0       0           0            0        0   
8505         1           0       0           0            1        0   
8523         1           0       0           0            0        1   

     cored_score diffuse_score cg_score CAA_score  cored_pred2  
90           0.0      0.678247        1       0.0            1  
208     0.653464           0.0        0       0.0            1  
779     0.662577           0.0        0  0.732042            1  
904          0.0           0.0        1       0.0            1  
1049    0.598067           0.0        0       0.0            1  
...          ...           ...      ...       ...          ...  
8440         0.0           0.0        0  0.786813            0  
8479         0.0       0.82259        0  0.847852            0  
8502         0.0           0.0        0       0.0            0  
8505         0.0      0.792613        0       0.0            0  
8523         0.0           0.0        0  0.853955            0  

[2521 rows x 20 columns]

In [150]:
len(cored1[cored1["cored_gt"]==cored1["cored_pred2"]])/len(cored1)

0.2923443078143594

In [151]:
cored1[cored1["cored_gt"]!=cored1["cored_pred2"]]

id                                         imagename  cored  \
2697  54047            NA4009-02_AB/NA4009-02_AB_25_34_83.jpg    1.0   
3923   6936             NA4072-02_AB/NA4072-02_AB_11_35_1.jpg    1.0   
3924   8407             NA4072-02_AB/NA4072-02_AB_11_36_1.jpg    1.0   
3928   3204             NA4072-02_AB/NA4072-02_AB_12_37_0.jpg    1.0   
3969  41178             NA4072-02_AB/NA4072-02_AB_15_37_2.jpg    1.0   
...     ...                                               ...    ...   
8440   9905  NA_4930_02_AB14-24/NA_4930_02_AB14-24_9_3_27.jpg    1.0   
8479   4933  NA_4930_02_AB14-24/NA_4930_02_AB14-24_9_7_15.jpg    1.0   
8502  22879  NA_4933_02_AB17-24/NA_4933_02_AB17-24_11_6_2.jpg    1.0   
8505   5367  NA_4933_02_AB17-24/NA_4933_02_AB17-24_11_7_1.jpg    1.0   
8523   4785  NA_4933_02_AB17-24/NA_4933_02_AB17-24_14_5_1.jpg    1.0   

       diffuse  CAA  negative      flag  notsure                 imagename2  \
2697  1.368421  0.0       0.0  0.368421      0.0      NA4009-02_AB_25_34_83   
3923  0.000000  0.0       0.0  1.000000      0.0       NA4072-02_AB_11_35_1   
3924  0.000000  0.0       0.0  0.000000      0.0       NA4072-02_AB_11_36_1   
3928  0.000000  0.0       0.0  0.000000      0.0       NA4072-02_AB_12_37_0   
3969  0.000000  0.0       0.0  0.000000      0.0       NA4072-02_AB_15_37_2   
...        ...  ...       ...       ...      ...                        ...   
8440  0.596367  0.0       0.0  0.000000      0.0  NA_4930_02_AB14-24_9_3_27   
8479  0.066406  0.0       0.0  0.000000      0.0  NA_4930_02_AB14-24_9_7_15   
8502  0.000000  0.0       0.0  0.000000      0.0  NA_4933_02_AB17-24_11_6_2   
8505  0.000000  0.0       0.0  0.000000      0.0  NA_4933_02_AB17-24_11_7_1   
8523  0.000000  0.0       0.0  0.000000      0.0  NA_4933_02_AB17-24_14_5_1   

      cored_gt  diffuse_gt  CAA_gt  cored_pred diffuse_pred CAA_pred  \
2697         1           1       0           0            1        0   
3923         1           0       0           0            0        1   
3924         1           0       0           0            1        0   
3928         1           0       0           0            1        0   
3969         1           0       0           0            1        0   
...        ...         ...     ...         ...          ...      ...   
8440         1           0       0           0            0        1   
8479         1           0       0           0            1        1   
8502         1           0       0           0            0        0   
8505         1           0       0           0            1        0   
8523         1           0       0           0            0        1   

     cored_score diffuse_score cg_score CAA_score  cored_pred2  
2697         0.0       0.96106        0       0.0            0  
3923         0.0           0.0        0  0.414681            0  
3924         0.0      0.633487        0       0.0            0  
3928         0.0      0.392969        0       0.0            0  
3969         0.0      0.779842        0       0.0            0  
...          ...           ...      ...       ...          ...  
8440         0.0           0.0        0  0.786813            0  
8479         0.0       0.82259        0  0.847852            0  
8502         0.0           0.0        0       0.0            0  
8505         0.0      0.792613        0       0.0            0  
8523         0.0           0.0        0  0.853955            0  

[1784 rows x 20 columns]

In [127]:
notna_gt_train_df["cored_gt"] = notna_gt_train_df["cored"].apply(lambda l: 1 if l>=1 else 0)

/tmp/ipykernel_14394/1139365046.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [128]:
notna_gt_train_df

id                                          imagename  cored  \
0         0           NA4009-02_AB/neg_NA4009-02_AB_0_10_4.jpg    0.0   
1         0           NA4009-02_AB/neg_NA4009-02_AB_0_11_2.jpg    0.0   
2         0           NA4009-02_AB/neg_NA4009-02_AB_0_16_2.jpg    0.0   
3         0           NA4009-02_AB/neg_NA4009-02_AB_0_25_2.jpg    0.0   
4     19548             NA4009-02_AB/NA4009-02_AB_10_10_14.jpg    0.0   
...     ...                                                ...    ...   
8625      0  NA_4933_02_AB17-24/neg_NA_4933_02_AB17-24_9_19...    0.0   
8626      0  NA_4933_02_AB17-24/neg_NA_4933_02_AB17-24_9_27...    0.0   
8627  33873    NA_4933_02_AB17-24/NA_4933_02_AB17-24_9_3_1.jpg    0.0   
8628      0  NA_4933_02_AB17-24/neg_NA_4933_02_AB17-24_9_3_...    0.0   
8629   8617    NA_4933_02_AB17-24/NA_4933_02_AB17-24_9_6_1.jpg    0.0   

       diffuse  CAA  negative  flag  notsure                     imagename2  \
0     0.000000  0.0       1.0   0.0      0.0        neg_NA4009-02_AB_0_10_4   
1     0.000000  0.0       1.0   0.0      0.0        neg_NA4009-02_AB_0_11_2   
2     0.000000  0.0       1.0   0.0      0.0        neg_NA4009-02_AB_0_16_2   
3     0.000000  0.0       1.0   0.0      0.0        neg_NA4009-02_AB_0_25_2   
4     2.653226  0.0       0.0   1.0      0.0          NA4009-02_AB_10_10_14   
...        ...  ...       ...   ...      ...                            ...   
8625  0.000000  0.0       1.0   0.0      0.0  neg_NA_4933_02_AB17-24_9_19_0   
8626  0.000000  0.0       1.0   0.0      0.0  neg_NA_4933_02_AB17-24_9_27_4   
8627  1.000000  0.0       0.0   0.0      0.0       NA_4933_02_AB17-24_9_3_1   
8628  0.000000  0.0       1.0   0.0      0.0   neg_NA_4933_02_AB17-24_9_3_4   
8629  0.000000  0.0       1.0   0.0      0.0       NA_4933_02_AB17-24_9_6_1   

      cored_gt  diffuse_gt  CAA_gt  cored_pred diffuse_pred CAA_pred  \
0            0           0       0           0            0        0   
1            0           0       0           0            0        0   
2            0           0       0           0            0        0   
3            0           0       0           0            0        0   
4            0           1       0           0            1        0   
...        ...         ...     ...         ...          ...      ...   
8625         0           0       0           0            0        0   
8626         0           0       0           0            0        0   
8627         0           1       0           0            0        0   
8628         0           0       0           0            1        0   
8629         0           0       0           0            0        1   

     cored_score diffuse_score cg_score CAA_score  cored_pred2  
0            0.0           0.0        0       0.0            0  
1            0.0           0.0        0       0.0            0  
2            0.0           0.0        0       0.0            0  
3            0.0           0.0        0       0.0            0  
4            0.0      0.843813        0       0.0            0  
...          ...           ...      ...       ...          ...  
8625         0.0           0.0        0       0.0            0  
8626         0.0           0.0        0       0.0            0  
8627         0.0           0.0        0       0.0            0  
8628         0.0      0.934218        0       0.0            0  
8629         0.0           0.0        0    0.6184            0  

[70000 rows x 20 columns]

In [34]:
# excluding NA values from train
#notna_gt_train_df = gt_train_df[~gt_train_df["cored_pred"].isna()]

In [ ]:
# Concatenate train and val outputs
final_df = pd.concat([notna_gt_train_df,notna_gt_val_df], ignore_index=True)

In [19]:
final_df=notna_gt_train_df

In [20]:
final_df

id                                          imagename  cored  \
0          0           NA4009-02_AB/neg_NA4009-02_AB_0_10_4.jpg    0.0   
1          0           NA4009-02_AB/neg_NA4009-02_AB_0_11_2.jpg    0.0   
2          0           NA4009-02_AB/neg_NA4009-02_AB_0_16_2.jpg    0.0   
3          0           NA4009-02_AB/neg_NA4009-02_AB_0_25_2.jpg    0.0   
4      19548             NA4009-02_AB/NA4009-02_AB_10_10_14.jpg    0.0   
...      ...                                                ...    ...   
61365      0  NA_4888_02_AB17-24/neg_NA_4888_02_AB17-24_9_5_...    0.0   
61366      0  NA_4888_02_AB17-24/neg_NA_4888_02_AB17-24_9_7_...    0.0   
61367  19688    NA_4888_02_AB17-24/NA_4888_02_AB17-24_9_9_2.jpg    0.0   
61368  19689    NA_4888_02_AB17-24/NA_4888_02_AB17-24_9_9_3.jpg    0.0   
61369  19690    NA_4888_02_AB17-24/NA_4888_02_AB17-24_9_9_4.jpg    0.0   

        diffuse  CAA  negative  flag  notsure                    imagename2  \
0      0.000000  0.0       1.0   0.0      0.0       neg_NA4009-02_AB_0_10_4   
1      0.000000  0.0       1.0   0.0      0.0       neg_NA4009-02_AB_0_11_2   
2      0.000000  0.0       1.0   0.0      0.0       neg_NA4009-02_AB_0_16_2   
3      0.000000  0.0       1.0   0.0      0.0       neg_NA4009-02_AB_0_25_2   
4      2.653226  0.0       0.0   1.0      0.0         NA4009-02_AB_10_10_14   
...         ...  ...       ...   ...      ...                           ...   
61365  0.000000  0.0       1.0   0.0      0.0  neg_NA_4888_02_AB17-24_9_5_3   
61366  0.000000  0.0       1.0   0.0      0.0  neg_NA_4888_02_AB17-24_9_7_2   
61367  1.815789  0.0       0.0   0.0      0.0      NA_4888_02_AB17-24_9_9_2   
61368  1.653846  0.0       0.0   0.0      0.0      NA_4888_02_AB17-24_9_9_3   
61369  1.000000  0.0       0.0   0.0      0.0      NA_4888_02_AB17-24_9_9_4   

       cored_gt  diffuse_gt  CAA_gt  cored_pred  diffuse_pred  CAA_pred  \
0             0           0       0           0             0         0   
1             0           0       0           0             0         0   
2             0           0       0           0             0         0   
3             0           0       0           0             0         0   
4             0           1       0           0             1         0   
...         ...         ...     ...         ...           ...       ...   
61365         0           0       0           0             1         0   
61366         0           0       0           0             0         0   
61367         0           1       0           0             1         0   
61368         0           1       0           0             1         0   
61369         0           1       0           0             1         0   

       cored_score  diffuse_score  cg_score  CAA_score  
0              0.0       0.000000         0        0.0  
1              0.0       0.000000         0        0.0  
2              0.0       0.000000         0        0.0  
3              0.0       0.000000         0        0.0  
4              0.0       0.843813         0        0.0  
...            ...            ...       ...        ...  
61365          0.0       0.915316         0        0.0  
61366          0.0       0.000000         0        0.0  
61367          0.0       0.914173         0        0.0  
61368          0.0       0.864961         0        0.0  
61369          0.0       0.942234         0        0.0  

[61370 rows x 19 columns]

In [160]:
#final_df =  pd.read_csv("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/classification_dataset/final_output_train_val_nature.csv")

In [161]:
final_df.head(2)

id                                 imagename  cored  diffuse  CAA  \
0   0  NA4009-02_AB/neg_NA4009-02_AB_0_10_4.jpg    0.0      0.0  0.0   
1   0  NA4009-02_AB/neg_NA4009-02_AB_0_11_2.jpg    0.0      0.0  0.0   

   negative  flag  notsure               imagename2  cored_gt  diffuse_gt  \
0       1.0   0.0      0.0  neg_NA4009-02_AB_0_10_4         0           0   
1       1.0   0.0      0.0  neg_NA4009-02_AB_0_11_2         0           0   

   CAA_gt  cored_pred diffuse_pred CAA_pred cored_score diffuse_score  \
0       0           0            0        0         0.0           0.0   
1       0           0            0        0         0.0           0.0   

  cg_score CAA_score  cored_pred2  
0        0       0.0            0  
1        0       0.0            0

In [162]:
final_df["cored_pred"] = np.where(final_df["cg_score"]>0,1, final_df["cored_pred"])

/tmp/ipykernel_14394/1558718014.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [21]:
final_df["cored_pred"]=final_df["cored_pred"].astype(int)

In [22]:
final_df["diffuse_pred"]=final_df["diffuse_pred"].astype(int)

In [23]:
final_df["CAA_pred"]=final_df["CAA_pred"].astype(int)

## Classification Metric - Core

In [24]:
final_df["cored_gt"].unique()

array([0, 1])

In [25]:
final_df["cored_pred"].unique()

array([0, 1])

In [26]:
notna_gt_train_df["cored_pred"] = notna_gt_train_df["cored_pred"].astype(int)

In [169]:
#tmp =  final_df[final_df["cored_gt"]>0]
#print(len(tmp))
#print(classification_report(tmp["cored_gt"], tmp["cored_pred"]))
print(classification_report(notna_gt_train_df["cored_gt"], notna_gt_train_df["cored_pred2"]))#

              precision    recall  f1-score   support

           0       0.97      0.87      0.91     67479
           1       0.07      0.29      0.12      2521

    accuracy                           0.84     70000
   macro avg       0.52      0.58      0.52     70000
weighted avg       0.94      0.84      0.89     70000



In [83]:
tmp = final_df[final_df["cored_gt"]!=final_df["cored_pred"]]
len(tmp[tmp["CAA_score"]>0.80])

2075

In [84]:
final_df[(final_df["CAA_gt"]>0) & (final_df["CAA_pred"]<=0)]

id                                          imagename  cored  \
778    2831              NA4009-02_AB/NA4009-02_AB_13_9_58.jpg    0.0   
1084   6766              NA4009-02_AB/NA4009-02_AB_16_18_0.jpg    0.0   
1085   6767              NA4009-02_AB/NA4009-02_AB_16_18_2.jpg    0.0   
6793  47852               NA4144-02_AB/NA4144-02_AB_3_21_3.jpg    0.0   
7502  12551               NA4144-02_AB/NA4144-02_AB_8_29_0.jpg    0.0   
...     ...                                                ...    ...   
7770  10151  NA_4930_02_AB14-24/NA_4930_02_AB14-24_5_26_15.jpg    0.0   
7771  10228   NA_4930_02_AB14-24/NA_4930_02_AB14-24_5_26_2.jpg    0.0   
7772   4313   NA_4930_02_AB14-24/NA_4930_02_AB14-24_5_26_5.jpg    0.0   
8338  32266  NA_4930_02_AB14-24/NA_4930_02_AB14-24_8_37_37.jpg    0.0   
8382   9443   NA_4930_02_AB14-24/NA_4930_02_AB14-24_9_15_5.jpg    0.0   

       diffuse       CAA  negative      flag   notsure  \
778   0.998043  1.000000       0.0  0.189189  0.263021   
1084  0.000000  1.000000       0.0  0.000000  0.000000   
1085  0.000000  1.000000       0.0  0.000000  0.000000   
6793  0.000000  1.000000       0.0  1.000000  0.000000   
7502  0.000000  1.000000       0.0  0.000000  0.000000   
...        ...       ...       ...       ...       ...   
7770  2.840000  0.997273       0.0  2.997273  0.000000   
7771  2.472353  2.000000       0.0  4.000000  0.000000   
7772  1.828419  2.000000       0.0  3.145161  0.000000   
8338  0.000000  1.000000       0.0  0.000000  0.000000   
8382  1.000000  0.333333       0.0  0.333333  0.000000   

                      imagename2  cored_gt  diffuse_gt  CAA_gt  cored_pred  \
778         NA4009-02_AB_13_9_58         0           1       1           0   
1084        NA4009-02_AB_16_18_0         0           0       1           0   
1085        NA4009-02_AB_16_18_2         0           0       1           0   
6793         NA4144-02_AB_3_21_3         0           0       1           0   
7502         NA4144-02_AB_8_29_0         0           0       1           0   
...                          ...       ...         ...     ...         ...   
7770  NA_4930_02_AB14-24_5_26_15         0           1       1           0   
7771   NA_4930_02_AB14-24_5_26_2         0           1       1           0   
7772   NA_4930_02_AB14-24_5_26_5         0           1       1           0   
8338  NA_4930_02_AB14-24_8_37_37         0           0       1           0   
8382   NA_4930_02_AB14-24_9_15_5         0           1       1           0   

      diffuse_pred  CAA_pred cored_score diffuse_score cg_score CAA_score  
778              1         0         0.0      0.608906        0       0.0  
1084             0         0         0.0           0.0        0       0.0  
1085             0         0         0.0           0.0        0       0.0  
6793             0         0         0.0           0.0        0       0.0  
7502             0         0         0.0           0.0        0       0.0  
...            ...       ...         ...           ...      ...       ...  
7770             1         0         0.0      0.745312        0       0.0  
7771             0         0         0.0           0.0        0       0.0  
7772             1         0         0.0      0.661893        0       0.0  
8338             0         0         0.0           0.0        0       0.0  
8382             0         0         0.0           0.0        0       0.0  

[1671 rows x 19 columns]

## Classification Metric - Diffuse

In [170]:
print(classification_report(final_df["diffuse_gt"], final_df["diffuse_pred"]))

              precision    recall  f1-score   support

           0       0.38      0.86      0.53     14394
           1       0.95      0.64      0.76     55606

    accuracy                           0.69     70000
   macro avg       0.66      0.75      0.65     70000
weighted avg       0.83      0.69      0.72     70000



## Classification Metric - CAA

In [171]:
print(classification_report(final_df["CAA_gt"], final_df["CAA_pred"]))

              precision    recall  f1-score   support

           0       0.98      0.79      0.87     67654
           1       0.07      0.46      0.12      2346

    accuracy                           0.78     70000
   macro avg       0.52      0.62      0.50     70000
weighted avg       0.95      0.78      0.85     70000



In [71]:
#final_df.to_csv("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/classification_dataset/final_output_train_val_nature.csv")

## ROC Curve

In [172]:
import plotly.graph_objects as go
from sklearn.metrics import roc_curve, auc


colors={"cored":'royalblue', "diffuse":'firebrick','CAA':"green"}
df = final_df

fig = go.Figure()
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

for class_name in ["cored","diffuse","CAA"]:
    fpr, tpr, _ = roc_curve(df[class_name + "_gt"], df[class_name+"_score"])
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=class_name, mode='lines',line=dict(color=colors[class_name], width=2)))

fig.update_layout(
    xaxis_title='False Positive Rate',
    yaxis_title='True Positive Rate',
    yaxis=dict(scaleanchor="x", scaleratio=1),
    xaxis=dict(constrain='domain'),
    width=700, height=700
)
fig.update_layout( plot_bgcolor='white', title="Receiver operating characteristic Curve")
fig.update_xaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.update_yaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.show()
#fig.write_html("ROC_Curve.html")

## Precision Recall Curve

In [173]:
df = final_df

fig = go.Figure()
colors={"cored":'royalblue', "diffuse":'firebrick','CAA':"green"}
for class_name in ["cored","diffuse","CAA"]:
    pr, rc, _ = precision_recall_curve(df[class_name + "_gt"], df[class_name+"_score"])
    rp = (df[class_name + "_gt"]).sum()/len(df)
    fig.add_trace(go.Scatter(x=rc, y=pr, name=class_name, mode='lines',line=dict(color=colors[class_name], width=2)))
    #fig.add_trace(go.Scatter(x=[0,1], y=[rp,rp], name=class_name+"_random", mode='lines',line=dict(color=colors[class_name], width=2,dash='dash')))
    #fig.add_shape(type='line', line=dict(dash='dash',color=colors[class_name]), x0=0, x1=1, y0=rp, y1=rp, name=class_name)

fig.update_layout(
    xaxis_title='Recall',
    yaxis_title='Precision',
    yaxis=dict(scaleanchor="x", scaleratio=1),
    xaxis=dict(constrain='domain'),
    width=700, height=700
)
fig.update_layout( plot_bgcolor='white',title="Precision-Recall Curve")
fig.update_xaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.update_yaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.show()
#fig.write_html("PR_Curve.html")